<a href="https://colab.research.google.com/github/javier-jaime/Route-Recommender/blob/main/Mexico_Municipal_Crime_2022.ipynb" target="_parent"><img src="https://colab.research.google.com/assets/colab-badge.svg" alt="Open In Colab"/></a>

In [15]:
# Import Libraries
!pip install folium
import pandas as pd
from geopy.geocoders import Nominatim
from google.colab import drive
from google.colab import files
import folium # map rendering library
from folium import plugins

In [2]:
# Mount Google Drive

drive.mount('/content/drive')

Mounted at /content/drive



Original Dataset from Mexico Government here:

https://www.gob.mx/sesnsp/acciones-y-programas/incidencia-delictiva-del-fuero-comun-nueva-metodologia

In [3]:
# Read dataset from excel in Google Drive to Pandas Data Frame
muni_crime_df = pd.read_excel('drive/MyDrive/Colab Data/Municipal_2022.xlsx')
print(muni_crime_df.shape)
muni_crime_df.head()

(242942, 21)


Año  Clave_Ent         Entidad  Cve. Municipio       Municipio  \
0  2022          1  Aguascalientes            1001  Aguascalientes   
1  2022          1  Aguascalientes            1001  Aguascalientes   
2  2022          1  Aguascalientes            1001  Aguascalientes   
3  2022          1  Aguascalientes            1001  Aguascalientes   
4  2022          1  Aguascalientes            1001  Aguascalientes   

             Bien jurídico afectado Tipo de delito  Subtipo de delito  \
0  La vida y la Integridad corporal      Homicidio   Homicidio doloso   
1  La vida y la Integridad corporal      Homicidio   Homicidio doloso   
2  La vida y la Integridad corporal      Homicidio   Homicidio doloso   
3  La vida y la Integridad corporal      Homicidio   Homicidio doloso   
4  La vida y la Integridad corporal      Homicidio  Homicidio culposo   

           Modalidad  Enero  ...  Marzo  Abril  Mayo  Junio  Julio  Agosto  \
0  Con arma de fuego      2  ...      2    NaN   NaN    NaN    NaN     NaN   
1    Con arma blanca      2  ...      1    NaN   NaN    NaN    NaN     NaN   
2  Con otro elemento      0  ...      0    NaN   NaN    NaN    NaN     NaN   
3    No especificado      0  ...      0    NaN   NaN    NaN    NaN     NaN   
4  Con arma de fuego      0  ...      0    NaN   NaN    NaN    NaN     NaN   

   Septiembre  Octubre  Noviembre  Diciembre  
0         NaN      NaN        NaN        NaN  
1         NaN      NaN        NaN        NaN  
2         NaN      NaN        NaN        NaN  
3         NaN      NaN        NaN        NaN  
4         NaN      NaN        NaN        NaN  

[5 rows x 21 columns]

In [4]:
# Drop Empty/NA cells
muni_crime_df = muni_crime_df.dropna(axis=1)
muni_crime_df.isnull().any()

Año                       False
Clave_Ent                 False
Entidad                   False
Cve. Municipio            False
Municipio                 False
Bien jurídico afectado    False
Tipo de delito            False
Subtipo de delito         False
Modalidad                 False
Enero                     False
Febrero                   False
Marzo                     False
dtype: bool

In [5]:
# Count of Unique Crime types
muni_crime_df['Tipo de delito'].value_counts()

Robo                                                                             89244
Homicidio                                                                        22311
Lesiones                                                                         22311
Secuestro                                                                        12395
Feminicidio                                                                       9916
Narcomenudeo                                                                      2479
Violencia de género en todas sus modalidades distinta a la violencia familiar     2479
Incumplimiento de obligaciones de asistencia familiar                             2479
Otros delitos contra la familia                                                   2479
Corrupción de menores                                                             2479
Trata de personas                                                                 2479
Otros delitos contra la sociedad           

In [6]:
# Count Unique Crime sub-types
muni_crime_df['Subtipo de delito'].value_counts()

Robo de maquinaria                                                               14874
Robo de vehículo automotor                                                       14874
Lesiones culposas                                                                12395
Secuestro                                                                        12395
Homicidio culposo                                                                12395
Homicidio doloso                                                                  9916
Lesiones dolosas                                                                  9916
Feminicidio                                                                       9916
Robo en transporte público individual                                             4958
Robo a transportista                                                              4958
Robo a transeúnte en vía pública                                                  4958
Robo a transeúnte en espacio abierto al púb

In [7]:
muni_crime_df['2022 AVG'] = (muni_crime_df['Enero'] + muni_crime_df['Febrero'] + muni_crime_df['Marzo']) / 3
muni_crime_df.drop(['Año','Clave_Ent', 'Cve. Municipio','Enero','Febrero','Marzo'], axis=1, inplace=True)
muni_crime_df.head()

/usr/local/lib/python3.7/dist-packages/ipykernel_launcher.py:1: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  """Entry point for launching an IPython kernel.
/usr/local/lib/python3.7/dist-packages/pandas/core/frame.py:4913: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  errors=errors,


Entidad       Municipio            Bien jurídico afectado  \
0  Aguascalientes  Aguascalientes  La vida y la Integridad corporal   
1  Aguascalientes  Aguascalientes  La vida y la Integridad corporal   
2  Aguascalientes  Aguascalientes  La vida y la Integridad corporal   
3  Aguascalientes  Aguascalientes  La vida y la Integridad corporal   
4  Aguascalientes  Aguascalientes  La vida y la Integridad corporal   

  Tipo de delito  Subtipo de delito          Modalidad  2022 AVG  
0      Homicidio   Homicidio doloso  Con arma de fuego  1.666667  
1      Homicidio   Homicidio doloso    Con arma blanca  1.666667  
2      Homicidio   Homicidio doloso  Con otro elemento  0.000000  
3      Homicidio   Homicidio doloso    No especificado  0.000000  
4      Homicidio  Homicidio culposo  Con arma de fuego  0.000000

In [8]:
# Group murders per State per Year
murders = muni_crime_df[muni_crime_df['Tipo de delito'] == 'Homicidio']
murders_per_state = murders.groupby(['Entidad']).sum().sort_values(by='2022 AVG')
murders_per_state.transpose()

Entidad   Baja California Sur  Tlaxcala  Aguascalientes   Campeche    Yucatán  \
2022 AVG                  7.0      13.0       13.666667  14.666667  18.333333   

Entidad     Durango  Coahuila de Zaragoza  Nayarit  Querétaro    Hidalgo  ...  \
2022 AVG  24.666667                  26.0     26.0       35.0  45.333333  ...   

Entidad   Oaxaca  Nuevo León  Sonora   Chihuahua  \
2022 AVG   129.0  133.666667   136.0  141.333333   

Entidad   Veracruz de Ignacio de la Llave     Jalisco  Baja California  \
2022 AVG                       161.666667  212.333333            215.0   

Entidad   Guanajuato  Michoacán de Ocampo  México  
2022 AVG  276.333333           298.666667   316.0  

[1 rows x 32 columns]

In [9]:
# Count Unique Municipalities
muni_crime_df['Municipio'].value_counts()

Benito Juárez            686
Ocampo                   588
Emiliano Zapata          588
No Especificado          490
Morelos                  490
                        ... 
Penjamillo                98
Pátzcuaro                 98
Paracho                   98
Parácuaro                 98
Santa María de la Paz     98
Name: Municipio, Length: 2331, dtype: int64

In [10]:
# Drop Non Specified and Other Municipalities 
muni_crime_df.drop(muni_crime_df[muni_crime_df['Municipio'] == 'No Especificado'].index, inplace = True)
muni_crime_df.drop(muni_crime_df[muni_crime_df['Municipio'] == 'Otros Municipios'].index, inplace = True)

# Replace long names Municipalities with shorter names 
muni_crime_df['Municipio'].replace('Rincón Chamula San Pedro','Rincón Chamula', inplace=True)
muni_crime_df['Municipio'].replace('Batopilas de Manuel Gómez Morín','Batopilas', inplace=True)
muni_crime_df['Municipio'].replace('Jonacatepec de Leandro Valle','Jonacatepec', inplace=True)
muni_crime_df['Municipio'].replace('Heroica Villa Tezoatlán de Segura y Luna, Cuna de la Independencia de Oaxaca','Tezoatlán', inplace=True)
muni_crime_df['Municipio'].replace('San Juan Mixtepec Distrito 08','San Juan Mixtepec', inplace=True)
muni_crime_df['Municipio'].replace('San Juan Mixtepec Distrito 26','San Juan Mixtepec', inplace=True)
muni_crime_df['Municipio'].replace('San Pedro Mixtepec Distrito 22','San Pedro Mixtepec', inplace=True)
muni_crime_df['Municipio'].replace('San Pedro Mixtepec Distrito 26','San Pedro Mixtepec', inplace=True)

In [11]:
# Create a Municipalities Table
munis = muni_crime_df.groupby(['Entidad','Municipio']).sum().round(decimals=2).reset_index()
munis

Entidad              Municipio  2022 AVG
0     Aguascalientes         Aguascalientes   2298.00
1     Aguascalientes               Asientos     74.00
2     Aguascalientes               Calvillo     69.67
3     Aguascalientes                  Cosío     40.00
4     Aguascalientes               El Llano     33.33
...              ...                    ...       ...
2464       Zacatecas  Villa González Ortega      4.67
2465       Zacatecas          Villa Hidalgo      8.33
2466       Zacatecas           Villa de Cos     23.00
2467       Zacatecas             Villanueva     31.00
2468       Zacatecas              Zacatecas    412.33

[2469 rows x 3 columns]

In [12]:
# Convert an address (Entidad, Municipio) into latitude and longitude values
address = input('Enter Adress/City, Province/State and/or Country: ')

geolocator = Nominatim(user_agent="mexico_explorer")
location = geolocator.geocode(address)
latitude = location.latitude
longitude = location.longitude
print('The geograpical coordinate of {} are {}, {}.'.format(address, latitude, longitude))

Enter Adress/City, Province/State and/or Country: 64 Healy Drive SW
The geograpical coordinate of 64 Healy Drive SW are 50.97860335, -114.07820984416779.


In [13]:
# Geo locate Municipalities
geolocator = Nominatim(user_agent="mexico_explorer")
Lat = []
Lon = []

for i in range(len(munis)):
  location = geolocator.geocode(munis['Municipio'][i]+', '+munis['Entidad'][i])
  # print('The geograpical coordinate of {} are {}, {}.'.format(i, latitude, longitude))
  Lat.append(location.latitude)
  Lon.append(location.longitude)

munis['Latitude'] = Lat
munis['Longitude'] = Lon

In [16]:
# create map of Mexico using latitude and longitude values
map_mexico = folium.Map(location=[25, -102], zoom_start=6)

# add markers to map
for lat, lon, State, Municipality in zip(munis['Latitude'], munis['Longitude'], munis['Entidad'], munis['Municipio']):
    label = '{}, {}'.format(State, Municipality)
    label = folium.Popup(label, parse_html=True)
    folium.CircleMarker(
        [lat, lon],
        radius=0.1,
        popup=label,
        color='red',
        fill=False,
        parse_html=False).add_to(map_mexico)  

heat_data = list(zip(munis['Latitude'], munis['Longitude'],munis['2022 AVG']))
plugins.HeatMap(heat_data, radius=20).add_to(map_mexico)
 
map_mexico

In [14]:
# Export Crime and location data back to Google Drive
muni_crime_df.to_csv('Municipal_Crime_2022.csv')
!cp Municipal_Crime_2022.csv "/content/drive/My Drive/Colab Data/"
munis.to_csv('Municipalities_Location_2022.csv')
!cp Municipalities_Location_2022.csv "/content/drive/My Drive/Colab Data/"